In [1]:
import json
from collections import defaultdict

# Read the JSON file
with open('all_tables_schemas.json', 'r') as f:
    schemas = json.load(f)

# Create a defaultdict to store the converted structure
converted_schemas = defaultdict(list)

# Convert the structure
for schema in schemas:
    table_name = schema['table_name']
    column_info = {
        'column_name': schema['column_name'],
        'data_type': schema['data_type']
    }
    converted_schemas[table_name].append(column_info)

# Convert defaultdict to regular dict and then to list of tuples
result = [(table_name, columns) for table_name, columns in converted_schemas.items()]

# Print the result
with open('all_tables_schemas_converted.json', 'w') as f:
    f.write(json.dumps(result, indent=4))

---

In [5]:
with open('/Users/ankamenskiy/SmartDota/src/data_new/fetched_datasets/public_matches__05-04-2025_05-05-2025_7-38с_rank60+_27.5k_.json', 'r') as f:
    data = json.load(f)['rows']

a = list(sorted(data, key=lambda x: x['match_id']))[::-1]
print([x['match_id'] for x in a][:10])

[8280820512, 8280819206, 8280818618, 8280817415, 8280817107, 8280815315, 8280813505, 8280813502, 8280812102, 8280809502]


In [6]:
a[0]

{'match_id': 8280820512,
 'radiant_win': False,
 'radiant_team': [138, 97, 86, 62, 32],
 'dire_team': [64, 18, 8, 121, 46]}

In [14]:
import requests
import json

def get_match_details(match_id, api_key):
    url = f"https://api.stratz.com/graphql?key={api_key}"

    # Prepare the full GraphQL query with match ID directly embedded
    query = f"""
    query GetMatchById {{
      match(id: {match_id}) {{
        id
        startDateTime
        didRadiantWin
        durationSeconds
        averageRank
        players {{
          steamAccount {{
            id
            name
          }}
          heroId
          isRadiant
          kills
          deaths
          assists
          networth
        }}
      }}
    }}
    """

    # Set headers including the required User-Agent
    headers = {
        "Content-Type": "application/json",
        "User-Agent": "STRATZ_API"
    }

    # Send POST request with JSON body
    response = requests.post(url, headers=headers, json={
        "query": query,
        "operationName": "GetMatchById"
    })

    # Raise error if something went wrong
    response.raise_for_status()

    # Return parsed JSON
    return response.json()


# Example usage:
if __name__ == "__main__":
    # Replace with desired match ID and your STRATZ API key
    match_id = 8280820512
    api_key = "jE1M9jZk28iOXJs2LBfrN3gxWeqfgR2B"  # ← Replace with your actual API key

    try:
        data = get_match_details(match_id, api_key)
        print(json.dumps(data, indent=2))
    except requests.exceptions.RequestException as e:
        print("HTTP error:", e)
    except Exception as e:
        print("Error:", e)

{
  "data": {
    "match": {
      "id": 8280820512,
      "startDateTime": 1746392329,
      "didRadiantWin": false,
      "durationSeconds": 2759,
      "averageRank": null,
      "players": [
        {
          "steamAccount": {
            "id": 136428875,
            "name": "Kubko"
          },
          "heroId": 138,
          "isRadiant": true,
          "kills": 4,
          "deaths": 10,
          "assists": 24,
          "networth": 13510
        },
        {
          "steamAccount": {
            "id": 178796711,
            "name": "Mario"
          },
          "heroId": 97,
          "isRadiant": true,
          "kills": 7,
          "deaths": 13,
          "assists": 16,
          "networth": 17347
        },
        {
          "steamAccount": {
            "id": 171077732,
            "name": "lapa"
          },
          "heroId": 86,
          "isRadiant": true,
          "kills": 18,
          "deaths": 8,
          "assists": 16,
          "networth": 25471
   

In [10]:
import json

with open('/Users/ankamenskiy/SmartDota/src/data_new/fetched_datasets/stratz_matches.json', 'r') as f:
    data = json.load(f)

In [11]:
cnt = 0
for elem in data["matches"]:
    if 'public' in elem:
        cnt += 1
print(cnt)

103


In [12]:
data['matches'][0]

{'id': 8242057914,
 'didRadiantWin': False,
 'startDateTime': 1743800411,
 'endDateTime': 1743802995,
 'actualRank': 62,
 'rank': 62,
 'players': [{'playerSlot': 0,
   'isRadiant': True,
   'heroId': 103,
   'kills': 6,
   'deaths': 12,
   'assists': 12,
   'numLastHits': 95,
   'numDenies': 2,
   'heroDamage': 19621,
   'heroHealing': 0,
   'steamAccount': {'id': 88805322,
    'isDotaPlusSubscriber': True,
    'dotaAccountLevel': 160,
    'smurfFlag': 0},
   'lane': 'OFF_LANE',
   'position': 'POSITION_4',
   'role': 'LIGHT_SUPPORT',
   'roleBasic': 'LIGHT_SUPPORT',
   'behavior': 0},
  {'playerSlot': 1,
   'isRadiant': True,
   'heroId': 104,
   'kills': 7,
   'deaths': 9,
   'assists': 13,
   'numLastHits': 300,
   'numDenies': 2,
   'heroDamage': 30437,
   'heroHealing': 1130,
   'steamAccount': {'id': 157765557,
    'isDotaPlusSubscriber': True,
    'dotaAccountLevel': 48,
    'smurfFlag': 0},
   'lane': 'MID_LANE',
   'position': 'POSITION_2',
   'role': 'CORE',
   'roleBasic': '

In [21]:
import json

with open('/Users/ankamenskiy/SmartDota/src/data_new/fetched_datasets/stratz_matches.json', 'r') as f:
    data = json.load(f)

In [24]:
import pandas as pd
import random
import copy

global no_role_cnt
no_role_cnt = 0

def flatten_steam_account(player_data):
    """Flatten the steamAccount dictionary."""
    steam_data = player_data.pop('steamAccount')
    for key, value in steam_data.items():
        player_data[f'{"steam_" if key == "id" else ""}{key}'] = value
    return player_data

def get_team_position(player_data):
    """Get team and position for a player."""
    team = 'radiant' if player_data['isRadiant'] else 'dire'
    if not player_data['position']:
        return team, None
    position = player_data['position'].lower().replace('position_', '')
    return team, f"{team}_{position}"

def convert_match_to_dataframe(match_data):
    """Convert a single match data structure to a pandas DataFrame."""
    # Extract base match info
    match_info = {
        'match_id': match_data['id'],
        'did_radiant_win': match_data['didRadiantWin'],
        'start_time': match_data['startDateTime'],
        'end_time': match_data['endDateTime'],
        'actualRank': match_data['actualRank'],
        'rank': match_data['rank']
    }
    
    # Initialize player positions with None
    player_positions = {
        'radiant_1': None, 'radiant_2': None, 'radiant_3': None, 'radiant_4': None, 'radiant_5': None,
        'dire_1': None, 'dire_2': None, 'dire_3': None, 'dire_4': None, 'dire_5': None
    }
    
    # Fill in player data
    for player in sorted(match_data['players'], key=lambda x: x['position'] is not None, reverse=True):
        # Get team_position identifier
        player = flatten_steam_account(player)
        team, team_pos = get_team_position(player)
        
        # Store player data in the corresponding position
        if team_pos is None:
            team_keys = [k for k, v in player_positions.items() if k.startswith(team) and v is None]
            team_pos = random.choice(team_keys)
            print(f"Player placed to random of {team_keys}")
            print(player)
            global no_role_cnt
            no_role_cnt += 1
        player_positions[team_pos] = player
    
    # Combine match info with player data
    result = {**match_info, **player_positions}
    
    return pd.DataFrame([result])

def convert_matches_to_dataframe(matches_data):
    """Convert a list of match data structures to a pandas DataFrame."""
    dfs = []
    for match in matches_data:
        if 'public' in match:
            continue
        
        df = convert_match_to_dataframe(match)
        dfs.append(df)
    
    return pd.concat(dfs, ignore_index=True)

pd.set_option('display.max_colwidth', None)
# Convert to DataFrame
df = convert_matches_to_dataframe(copy.deepcopy(data)["matches"])
print("Columns:", df.columns.tolist())
print('no_role_cnt', no_role_cnt)
df 

Player placed to random of ['radiant_1', 'radiant_2', 'radiant_3', 'radiant_4', 'radiant_5']
{'playerSlot': 0, 'isRadiant': True, 'heroId': 65, 'kills': 11, 'deaths': 11, 'assists': 16, 'numLastHits': 388, 'numDenies': 5, 'heroDamage': 39066, 'heroHealing': 0, 'lane': None, 'position': None, 'role': None, 'roleBasic': 'CORE', 'behavior': None, 'steam_id': 135189733, 'isDotaPlusSubscriber': True, 'dotaAccountLevel': 151, 'smurfFlag': 0}
Player placed to random of ['radiant_1', 'radiant_2', 'radiant_4', 'radiant_5']
{'playerSlot': 1, 'isRadiant': True, 'heroId': 49, 'kills': 8, 'deaths': 11, 'assists': 9, 'numLastHits': 357, 'numDenies': 11, 'heroDamage': 24289, 'heroHealing': 0, 'lane': None, 'position': None, 'role': None, 'roleBasic': 'CORE', 'behavior': None, 'steam_id': 119943268, 'isDotaPlusSubscriber': True, 'dotaAccountLevel': 213, 'smurfFlag': 0}
Player placed to random of ['radiant_1', 'radiant_2', 'radiant_4']
{'playerSlot': 2, 'isRadiant': True, 'heroId': 138, 'kills': 5, 'de

match_id  did_radiant_win  start_time    end_time  actualRank  rank  \
0      8242057914            False  1743800411  1743802995          62    62   
1      8242057915             True  1743800411  1743802059          62    62   
2      8242058511             True  1743800446  1743803777          71    71   
3      8242067418             True  1743800763  1743804601          72    72   
4      8242068517             True  1743800829  1743803252          54    54   
...           ...              ...         ...         ...         ...   ...   
27171  8273395701             True  1745929988  1745932042          63    63   
27172  8279228408            False  1746299150  1746302301          62    62   
27173  8279752700             True  1746340619  1746342744          62    62   
27174  8278310909            False  1746252349  1746255356          70    70   
27175  8271134718            False  1745764598  1745767592          61    61   

                                                                                                                                                                                                                                                                                                                                                                        radiant_1  \
0       {'playerSlot': 3, 'isRadiant': True, 'heroId': 57, 'kills': 8, 'deaths': 13, 'assists': 5, 'numLastHits': 265, 'numDenies': 20, 'heroDamage': 21794, 'heroHealing': 1247, 'lane': 'SAFE_LANE', 'position': 'POSITION_1', 'role': 'CORE', 'roleBasic': 'CORE', 'behavior': 0, 'steam_id': 93565827, 'isDotaPlusSubscriber': True, 'dotaAccountLevel': 108, 'smurfFlag': 0}   
1       {'playerSlot': 0, 'isRadiant': True, 'heroId': 109, 'kills': 11, 'deaths': 2, 'assists': 12, 'numLastHits': 201, 'numDenies': 31, 'heroDamage': 22489, 'heroHealing': 0, 'lane': 'SAFE_LANE', 'position': 'POSITION_1', 'role': 'CORE', 'roleBasic': 'CORE', 'behavior': 0, 'steam_id': 1255582750, 'isDotaPlusSubscriber': False, 'dotaAccountLevel': 1, 'smurfFlag': 0}   
2        {'playerSlot': 1, 'isRadiant': True, 'heroId': 46, 'kills': 19, 'deaths': 5, 'assists': 14, 'numLastHits': 549, 'numDenies': 15, 'heroDamage': 63510, 'heroHealing': 0, 'lane': 'SAFE_LANE', 'position': 'POSITION_1', 'role': 'CORE', 'roleBasic': 'CORE', 'behavior': 0, 'steam_id': 176155866, 'isDotaPlusSubscriber': False, 'dotaAccountLevel': 45, 'smurfFlag': 0}   
3       {'playerSlot': 1, 'isRadiant': True, 'heroId': 114, 'kills': 18, 'deaths': 10, 'assists': 20, 'numLastHits': 506, 'numDenies': 8, 'heroDamage': 59284, 'heroHealing': 0, 'lane': 'SAFE_LANE', 'position': 'POSITION_1', 'role': 'CORE', 'roleBasic': 'CORE', 'behavior': 0, 'steam_id': 836221477, 'isDotaPlusSubscriber': True, 'dotaAccountLevel': 100, 'smurfFlag': 0}   
4          {'playerSlot': 4, 'isRadiant': True, 'heroId': 41, 'kills': 13, 'deaths': 3, 'assists': 9, 'numLastHits': 279, 'numDenies': 7, 'heroDamage': 32575, 'heroHealing': 0, 'lane': 'SAFE_LANE', 'position': 'POSITION_1', 'role': 'CORE', 'roleBasic': 'CORE', 'behavior': 0, 'steam_id': 120788323, 'isDotaPlusSubscriber': False, 'dotaAccountLevel': 89, 'smurfFlag': 0}   
...                                                                                                                                                                                                                                                                                                                                                                           ...   
27171        {'playerSlot': 3, 'isRadiant': True, 'heroId': 6, 'kills': 6, 'deaths': 3, 'assists': 7, 'numLastHits': 186, 'numDenies': 8, 'heroDamage': 13236, 'heroHealing': 0, 'lane': 'SAFE_LANE', 'position': 'POSITION_1', 'role': 'CORE', 'roleBasic': 'CORE', 'behavior': 0, 'steam_id': 192939041, 'isDotaPlusSubscriber': False, 'dotaAccountLevel': 72, 'smurfFlag': 0}   
27172    {'playerSlot': 4, 'isRadiant': True, 'heroId': 19, 'kil

In [28]:
df[['actualRank']]

actualRank
0              62
1              62
2              71
3              72
4              54
...           ...
27171          63
27172          62
27173          62
27174          70
27175          61

[27176 rows x 1 columns]

In [29]:
df[:1].to_json("/Users/ankamenskiy/SmartDota/src/experiments/src/transformers/data_sample.json", orient="records", lines=True)

In [30]:
pd.Timestamp.now() - pd.Timestamp.now() + pd.Timedelta(hours=6)

Timedelta('0 days 06:00:00')

In [ ]:
ts = pd.Timestamp(1746527284, unit='s')
hours_before_6 = ts - pd.Timedelta(hours=6)